# Linear regression with `scikit-learn`

Let us read again the `tips.csv` file.

In [ ]:
import pandas as pd

dtypes = {
    "sex": "category",
    "smoker": "category",
    "day": "category",
    "time": "category"
} 

df = pd.read_csv("tips.csv", dtype=dtypes)
df.head()

Let's perform one-hot encoding

In [ ]:
df_one_hot = pd.get_dummies(df, prefix_sep='#', drop_first=True)
df_one_hot.head()

## Separate the features and the label

In [ ]:
# We test in case we run several times this cell
if 'tip' in df_one_hot:
    tip = df_one_hot["tip"]
    df_one_hot.drop("tip", inplace=True, axis="columns")

In [ ]:
df_one_hot.head()

In [ ]:
tip

## Train a linear regression model using `scikit-learn`

Using the `scikit-learn` library, we train a linear regression model to predict the tip

In [ ]:
from sklearn.linear_model import LinearRegression

# The features matrix is data and the labels vector is tip
X, y = df_one_hot, tip

# Create and train a linear regression
linreg = LinearRegression().fit(X, y)

`LinearRegression` is a class from `scikit-learn` allowing to train a linear regression model. 
Let's have a look at its main options.

In [ ]:
?LinearRegression

Once it is **fitted** using `fit`, it contains attributes which ends with a `_`. 
These attributes were obtained after the fit, namely they were **trained**.

In [ ]:
linreg.coef_

In [ ]:
linreg.intercept_

In [ ]:
linreg.n_features_in_

## About the `scikit-learn` API

(API = **A**pplication **P**rogramming **I**nterface).
One of the main reasons of the huge success of the `scikit-learn` library is its API and ease of use.
Mainly all the classes share the same methods:
- `transform` to transform data
- `fit` to fit an algorithm on data
- `fit_transform` to first `fit` then `transform`
- `predict` to give predictions

## Let's plot the model weights

In [ ]:
import numpy as np
import matplotlib.pyplot as plt

%matplotlib inline

plt.figure(figsize=(8, 4))
plt.title('Linear regression coefficients for tips prediction', 
          fontsize=16)
plt.stem(linreg.coef_, use_line_collection=True)
_ = plt.xticks(np.arange(linreg.coef_.shape[0]), df_one_hot.columns,
               rotation='vertical', fontsize=14)
_ = plt.yticks(fontsize=14)

What we observe is somewhat very weird: why `total_bill` is not the most important feature here ? 
This seems counter-intuitive!

- We would expect the `'total_bill'` feature to have a strong impact on the prediction, but the weight associated to it is small compared to the other ones

The problem comes from the fact that we **did not normalize the continuous features** before training this linear regression

- The `'total_bill'` column is not normalized, and takes values that are arbitrarily larger than the dummies

So, let's try again with a min-max normalization (puts features between 0 and 1).

## Training again with normalized features

Let's normalize the features using a "scaler" from `scikit-learn` and train again the linear regression

In [ ]:
from sklearn.preprocessing import StandardScaler

scaler = StandardScaler()
X_rescaled = scaler.fit_transform(X)
linreg = LinearRegression().fit(X_rescaled, y)

plt.figure(figsize=(8, 4))
plt.title('Linear regression coefficients for tips prediction', 
          fontsize=16)
plt.stem(linreg.coef_, use_line_collection=True)
_ = plt.xticks(np.arange(linreg.n_features_in_), df_one_hot.columns,
               rotation='vertical', fontsize=14)
_ = plt.yticks(fontsize=14)

This is much more intuitive: a larger total bill leads to a larger tip, and it is indeed the most important feature.<br>
But what is doing exactly `StandardScaler()` ?

- `StandardScaler.fit` computes the mean and variance of each column
- `StandardScaler.transform` standardizes each column by substracting the mean and by dividing by the standard-deviation
- `StandardScaler.fit_transform` is `StandardScaler.fit` followed by `StandardScaler.transform`

In [ ]:
?scaler

In [ ]:
scaler.n_features_in_

In [ ]:
scaler.n_samples_seen_

In [ ]:
scaler.mean_

In [ ]:
scaler.var_

## `scikit-learn` pipelines

Transformations and data-fitting operations can be **grouped together** in `scikit-learn` using a `Pipeline`.
This is extremely convenient in order to avoid mistakes such as :
- oooops! I forgot to scale the features become asking for predictions...

and it allows to organize your code

In [ ]:
from sklearn.pipeline import Pipeline

predictor = Pipeline([
    # We first scale the features
    ("scaler", StandardScaler()),
    # Then we train a linear predictor using the scaled features 
    #   (labels are left unchanged)
    ("linreg", LinearRegression())
])

In [ ]:
predictor.steps

In [ ]:
predictor["linreg"]

In [ ]:
predictor["scaler"]

In [ ]:
# Note that we use X and not X_rescaled here
predictor.fit(X, y)

plt.figure(figsize=(8, 4))
plt.title('Linear regression coefficients for tips prediction', 
          fontsize=16)
plt.stem(predictor["linreg"].coef_, use_line_collection=True)
_ = plt.xticks(np.arange(predictor.n_features_in_), df_one_hot.columns,
               rotation='vertical', fontsize=14)
_ = plt.yticks(fontsize=14)

## Assessment of the linear predictor

This is nice, but how do I know if my linear predictor is **any good** ?
In machine learning, assessment always require **cross-validation**. As a start, let's use the simplest cross-validation strategy: **train-test splitting**: we just divide our data into two disjoint pieces.

In [ ]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=42)

In [ ]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

By default, `train_test_split` using 25% of the data for **testing** and 75% for **training**, hence the $244 \times 0.75 = 183$ rows for training and $244 \times 0.25 = 61$ for **testing**

In [ ]:
predictor = Pipeline([
    ("scaler", StandardScaler()),
    ("linreg", LinearRegression())
])
# This time, we split using only the training data
predictor.fit(X_train, y_train)
# And predict the label (the tip) of the testing data
y_pred_test = predictor.predict(X_test)

Now, we can **compare** the predictions we obtained with the ground truth !

In [ ]:
fig, (ax0, ax1) = plt.subplots(nrows=1, ncols=2, figsize=(12, 4))

ax0.plot(np.linspace(0.5, 5.5, 1000), np.linspace(0, 6, 1000))
ax0.scatter(y_test, y_pred_test)
ax0.set_title("Predictions VS ground truth on test data", fontsize=14)
ax0.set_xlabel("Ground truth", fontsize=12)
ax0.set_ylabel("Predictions", fontsize=12)

ax1.stem(y_test - y_pred_test)
ax1.set_xlabel("Index of the test sample", fontsize=12)
ax1.set_ylabel("Ground truth - predictions", fontsize=12)

Not so bad for a first attempt. What about the training data ?

In [ ]:
y_pred_train = predictor.predict(X_train)

fig, (ax0, ax1) = plt.subplots(nrows=1, ncols=2, figsize=(12, 4))

ax0.plot(np.linspace(0, 10, 1000), np.linspace(0, 6, 1000))
ax0.scatter(y_train, y_pred_train)
ax0.set_title("Predictions VS ground truth on test data", fontsize=14)
ax0.set_xlabel("Ground truth", fontsize=12)
ax0.set_ylabel("Predictions", fontsize=12)

ax1.stem(y_train - y_pred_train)
ax1.set_xlabel("Index of the test sample", fontsize=12)
ax1.set_ylabel("Ground truth - predictions", fontsize=12)

We are **strongly over-estimating the tip** on the training data ! This is certainly coming from the outliers (customers that tip like crazy), that we need to remove from the data.

## Computing metrics to assess our predictor

Let's compute all the standard metrics for regression, cf <br>
https://scikit-learn.org/stable/modules/model_evaluation.html#regression-metrics

In [ ]:
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error

r2_scores = [
    r2_score(y_train, y_pred_train), 
    r2_score(y_test, y_pred_test)
]
abs_errors = [
    mean_absolute_error(y_train, y_pred_train), 
    mean_absolute_error(y_test, y_pred_test)
]
square_errors = [
    mean_squared_error(y_train, y_pred_train), 
    mean_squared_error(y_test, y_pred_test)
]

pd.DataFrame({
    "r2_score": r2_scores,
    "abs_error": abs_errors,
    "square_error": square_errors
}, index=["train", "test"])

**Pro tip.** Pro version of the cell above, with no copy/pasting (hence less prone to errors when typing) and using the full power of `python`'s syntax is as follows, using a `dict` comprehension:

In [ ]:
pd.DataFrame({
    score_name: [score(y_train, y_pred_train), score(y_test, y_pred_test)]
    for (score_name, score)
    in zip(["r2_score", "abs_error", "square_error"], 
           [r2_score, mean_absolute_error, mean_squared_error])
}, index=["train", "test"])

## Things that can be done from here

- Remove outliers (corresponding to tip percentages larger than, say, 30%), retrain and assess

Then, we can do some **features engineering** to try to improve the predictor:

- Use `size` as a categorical variable
- Compute the cartesian product of `sex` and `smoker` to create a new categorical feature describing the client. Do the same for `day` and `time`
- Using the `PolynomialFeatures` transformer from `sklearn.preprocessing` to create features that are polynomials of the original one (for `total_bill` but even others...)

For each version of your features engineering, retrain the model and compare between them